## Before We Start...

Basic concepts of Spark: 
- RDD (Resilient Distributed Datasets): fundamental data structure for distributing data among cluster nodes. Immutable.
- Transformation: operations on RDD that returns an RDD, such as map, filter, reduce, and reduceByKey.
- Action: operations on RDD that returns a non-RDD value, such as collect.

We will be mainly using Spark Dataframe APIs instead of RDD APIs, to simplify development.
- Spark Dataframes are very similar to tables in relational databases. They have schema. Most of the operations on them are similar to querying a relational database as well. You can consider Spark Dataframe as a wrap on top of RDD.

## Loading Data

In [0]:
# Reading data from Delta Lake

amazon_review_raw = spark.sql("SELECT * FROM default.reviews_train").sample(0.25)

In [0]:
display(amazon_review_raw)

reviewID overall verified reviewTime reviewerID asin reviewerName reviewText summary unixReviewTime label 4 3.0 true 05 7, 2015 A3B6GKQQ1JJ167 0560467893 Harry Slaughter Pretty flimsy, but does the job. If your corner is not square and flat, the shelves will probably not end up level. These shelves should probably be going for half the price. Meh 1430956800 1 7 5.0 true 01 24, 2016 A324TTUBKTN73A 0001713353 Tekla Borner My students (3 & 4 year olds) loved this book! Definitely recommend it to other teachers. Five Stars 1453593600 0 9 1.0 true 10 30, 2013 A7JVZFSXVY9RL 0681795107 Nickleen I like my coffee hot; borderline scorching but drinkable. About 10 years ago I purchased several Avantro coffee mugs that are very similar to these. Those have been able to keep my coffee at my preferred drinking temperature for well over 4 hours even on the coldest of days. I work outside so hot coffee is crucial in these nasty New England winters. Well, day one with this new mug and I am quite disappointed. This mug barely kept my coffee warm for an hour. That is quite unacceptable seeing as how this company is the one that bought out Avantro. Not keeping coffee hot for long enough 1383091200 0 11 2.0 true 02 20, 2015 A2204E1TH211HT 0700026657 Grandma KR found the game a bit too complicated, not what I expected after having played 1602, 1503, and 1701 Two Stars 1424390400 0 20 1.0 false 08 2, 2014 A1KXJ1ELZIU05C 0700026657 Creation27 I'm an avid gamer, but Anno 2070 is an INSULT to gaming. It is so buggy and half-finished that the first campaign doesn't even work properly and the DRM is INCREDIBLY frustrating to deal with. Once you manage to work your way past the massive amounts of bugs and get through the DRM, HOURS later you finally figure out that the game has no real tutorial, so you stuck just clicking around randomly. Sad, sad, sad, example of a game that could have been great but FTW. Avoid This Game - Filled with Bugs 1406937600 0 21 5.0 true 04 6, 2012 AO84V2TFRX9OB 0681795107 Meddybempster These mugs do what they are designed to do, i.e., keep liquids hot or cold for hours, don't leak, easy to clean and attractive to look at. But, do not put them in the dishwasher as they lose their magic! Keeps your drinks hot or cold for hours 1333670400 0 25 5.0 true 12 27, 2012 A2M46WTE5TR5WN 0001713353 SLL This was one of my favorites when I was a small child, so I bought a copy for my nephew when he was just starting to read. A Favorite 1356566400 0 28 5.0 false 08 15, 2011 ATHTCOG6BB6WK 0001713353 L. Williams So, you think you have problems? Things could be worse and this clever book can prove it. The king starts out with a problem. The mice are eating his cheese. The more he tries to fix the problem, the worse it gets. The king finally arranges to bring back the mice when he comes to the realization that his original dilemma wasn't so intolerable after all. The solution requires cooperation from the king and the mice. It involves the cheese. Maybe It's Not As Bad As You Think 1313366400 0 30 4.0 true 02 15, 2012 A345HVYNQJUGQM 0768205921 JenJen This is a great learning tool for teaching children how to tell time. The numbers are printed clearly and easy to read, including the seconds. The hands are easy to move. There is a piece on the back that can be used to prop up the clock, and the piece can pop off easily. It is easy to put back on though. I also ordered the "Telling Time with the Judy Clock" workbook. The little booklet that comes with the Judy clock has a lot of the same pages as the workbook, but it's a lot smaller. The "Telling Time" workbook gives children a lot more practice with learning to tell time. Great learning tool 1329264000 1 35 5.0 true 08 14, 2011 AN3YYDZAS3O1Y 0700099867 Bob Loved playing Dirt 2 and I thought the graphics were good. Purchased Dirt 3 as an addition to the other...and the graphics are absolutely "Gorgeous" If you liked Dirt or Dirt 2...you are going to love Dirt 3. The game was easier to configure wit

## Cleaning Data

In [0]:
# Drop duplicates

print("Before duplication removal: ", amazon_review_raw.count())
amazon_review_distinct = amazon_review_raw.dropDuplicates(['reviewerID', 'asin'])
print("After duplication removal: ", amazon_review_distinct.count())

Before duplication removal:  786160
After duplication removal:  770578


In [0]:
# Convert Unix timestamp to readable date

from pyspark.sql.functions import from_unixtime, to_date
from pyspark.sql.types import *

amazon_review_with_date = amazon_review_distinct.withColumn("reviewTime", to_date(from_unixtime(amazon_review_distinct.unixReviewTime))) \
                                                .drop("unixReviewTime")

In [0]:
display(amazon_review_with_date)

reviewID overall verified reviewTime reviewerID asin reviewerName reviewText summary label 1202645 5.0 true 2015-08-12 A0001528BGUBOEVR6T5U B000GWG0T2 igozingo super nice... Five Stars 0 2740967 5.0 true 2014-09-12 A0001528BGUBOEVR6T5U B002MF3CZG igozingo Very real Five Stars 0 1988039 5.0 true 2015-10-11 A00231762M7PUF3V3ZBI B0013LJA0Q Cassie Bought 2 of these for a white trash themed party to cover the designated restroom doors. A bit short for a standard door, material is like a plastic tablecloth. Taped onto the doors easily, just made a hole to allow the doorknob to go through. The price is right for what it is! A good value for a fun prop! 0 2344349 5.0 true 2017-10-23 A0034986DWR7WEDQN0GV B001ASRFCC oliver chong superb Five Stars 0 1109918 5.0 true 2014-02-10 A0090495K0FTJUG4CPSA 0030565073 Serenity I'd been wanting to read this for a while now, glad I did. Now I keep wanting to shout, it's a warning, not a Damn blueprint. classic for a reason 0 2594294 5.0 true 2014-10-07 A0103047AS0C8QKUI0X2 B001V9VDP0 Becky Tompkins Keeps my coffee beans fresh - holds plenty. Five Stars 0 233055 4.0 true 2016-12-07 A0122375SQ8Z42DUL03J B00005NCWV Retired Lady I really like the sturdiness of the pan, cups and lid. The eggs I poached came out perfectly. My only complaint or caution is that when I went to retrieve a cooked egg in the little cup, I scalded my fingers since the steam holes are right next to the little finger holds you use to get the individual cups out of the pan. I learned to use a pot holder or tong to retrieve the cup and save my fingers. I really like the sturdiness of the pan 0 2349148 5.0 true 2015-02-23 A0129009SMXEYR0W65IU B001AZH6H4 Teresa Clark I previously had ordered one & it worked prefect so I ordered 2 more, one for me and one for my daughter Great item one for me and one for my daughter Great 0 2812499 5.0 true 2013-08-25 A0139874ED7NYUB55TSR B00317DIEY Iryna This piece is very helpful and serves exactly as expected. This is a must-have in every household! I used it only once as it just arrived recently but it seems to be a great quality Amazing!!! 0 466759 5.0 true 2014-05-12 A0196552RI15HI7JB9PW B0000CDVD7 Matt Very heavy duty. It is very solid, it doesn't feel as though it would break easily. Presses garlic good, leaves some unpressed around the edges, but no more than other presses I've used Cleans easy which is a huge + Would recommend it I used to take 10 mins mincing up garlic really fine, but now I press it in 30s with the same (if not better) results Good product 0 2566780 5.0 true 2018-01-28 A0224041E58B9YLYXLOL B001T4ZAXI Greg Steinsultz Very thick....lol almost too thick... Good thickness 0 1032949 5.0 true 2017-11-23 A0239227GJ5Z0VBDC180 0025837109 Mr Ynot 3691 Good read Good read 0 2924120 5.0 true 2012-12-29 A0266076X6KPZ6CCHGVS B0053BG1EU Tyrel This game is fun and I would definitely recommend it to anyone who likes to dance and have fun . Just Dance 3 Review 0 3025032 5.0 false 2014-11-19 A0277912HT4JSJKVSL3E B00KSQHX1K Maria This was a great deal ! Brings back old memories when i used to play Halo 2 as a kid . Multiplayer works fine for me 60$ worth for 4 game in one ! This was a great deal! Brings back old memories when i used ... 1 3062792 5.0 false 2016-03-06 A02836981FYG9912C66F B00YQ2KCWO Weeble Wobble This game is fantastic. I can't believe I waited so long to get it. I didn't really like the other ones though. I have tried them all but for some reason I am addicted to this Fallout. I have spent at least 100+ hours so far in this game and only started playing it about 2 months ago. I beat it once as a Melee only character and then restarted as a charisma stealth player. WARNING: Do not complete the story entirely before completing missions in all 4 factions. If you DO complete it before you do all the missions then all of those missions will be lost. The first time I played I went all out in the story mode and only made it to level 40 by the end of it. This new time I am about half 

As comparison, for pandas dataframe you will use .apply() to apply a function to a column. See: https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.apply.html

For example: amz_review['Date'] = amz_review['Time'].apply(to_date)

In [0]:
# Tokenization

from pyspark.ml.feature import RegexTokenizer

regexTokenizer = RegexTokenizer(inputCol="reviewText", outputCol="reviewWord", pattern="\\W")

amazon_review_tokenized = regexTokenizer.transform(amazon_review_with_date.fillna("", subset=["reviewText"]))

In [0]:
# Remove stop words

from pyspark.ml.feature import StopWordsRemover

remover = StopWordsRemover(inputCol="reviewWord", outputCol="reviewWordFiltered")
amazon_review_stop_word_removed = remover.transform(amazon_review_tokenized)

In [0]:
# Stemming

from nltk.stem.porter import PorterStemmer
from pyspark.sql.functions import udf

def stemming(col):
    p_stemmer = PorterStemmer()
    return [p_stemmer.stem(w) for w in col]

stemming_udf = udf(stemming, ArrayType(StringType()))
amazon_review_stemmed = amazon_review_stop_word_removed.withColumn("reviewWordCleaned", stemming_udf(amazon_review_stop_word_removed.reviewWordFiltered))

In [0]:
# Dropping temporary columns, and cache results (note that cache is also a lazy operation)

amazon_review_cleaned = amazon_review_stemmed.drop("reviewWord").drop("reviewWordFiltered").cache()

display(amazon_review_cleaned)

reviewID overall verified reviewTime reviewerID asin reviewerName reviewText summary label reviewWordCleaned 984583 5.0 true 2018-05-07 A101RVZV3RBT8O B000BRU78C James Rizer heavy duty, great thermos. great thermos. 0 List(heavi, duti, great, thermo) 1726599 5.0 true 2016-01-06 A103CUDJVYLAHR B000UBO0IW Amazon Customer These were perfect. I have 4 grandchildren and I give each one an ornament each year. These just fit the bill. These were perfect. I have 4 grandchildren and I give each ... 0 List(perfect, 4, grandchildren, give, one, ornament, year, fit, bill) 2084214 5.0 true 2017-12-29 A104L4I6JM259S B0017XHSC2 Cory Stamm Works great Five Stars 0 List(work, great) 68080 5.0 true 2017-02-06 A1095ORFAE5XEA B00004RFM0 Cyrus Douglas The j. A. Henckels knives are very sharp. Just what I wanted The j. A. Henckels knives are very sharp ... 0 List(j, henckel, knive, sharp, want) 2330799 5.0 true 2014-12-28 A10AGLJYHNUKZA B001A60SXW Miss G Somehow there is a draft that is coming through my walls. How does that happen? I purchased these curtains for the insulation. They are a very close match to the color of my walls. Imagine a wall with 2 standard windows with the normal space between them. I hung the curtains on a rod stretched between the 2 windows. It actually looks nice (Not tacky like my daughter said it would.) More important, it cut the draft. No More Wall Draft 0 List(somehow, draft, come, wall, happen, purchas, curtain, insul, close, match, color, wall, imagin, wall, 2, standard, window, normal, space, hung, curtain, rod, stretch, 2, window, actual, look, nice, tacki, like, daughter, said, import, cut, draft) 2671361 3.0 true 2018-04-05 A10BUZFXQ3BXIC B002ACEGDS cgant This dresser had wonderful reviews compared to many others Ive read. Was feeling very optimistic about it. When it arrived it was very well packaged, but there were apparently a couple dings before being put in the packaging. It was generally a very easy dresser to assemble, took about 1 1/2-2hrs. The biggest disappointment though is the drawer size. The dresser itself is pretty deep, but the drawers are not. Will be trying to sell this now to get something else :( No sense in it taking up so much space in our smaller rooms for the storage capacity of a smaller dresser. Beautiful dresser,but disappointing 0 List(dresser, wonder, review, compar, mani, other, ive, read, feel, optimist, arriv, well, packag, appar, coupl, ding, put, packag, gener, easi, dresser, assembl, took, 1, 1, 2, 2hr, biggest, disappoint, though, drawer, size, dresser, pretti, deep, drawer, tri, sell, get, someth, els, sens, take, much, space, smaller, room, storag, capac, smaller, dresser) 2773118 4.0 true 2016-08-13 A10D6PSBCT0UQK B002T49E4I Robert R. great smell and works well but best with a little insect spray Four Stars 0 List(great, smell, work, well, best, littl, insect, spray) 1672667 2.0 false 2009-09-18 A10DCS8UQTNN7D 0060876115 Sara B. I won't go into how much I disliked the format of this story and how it took place simultaniously with the The Lost Duke of Wyndham, suffice it to say it make reading this book slow and repetitive and not as interesting as it could have been. I actually liked the characters of Thomas and Amelia better than Jack and Grace and felt they deserved a better, more in depth story line all their own, away from all the goings on in the first book. Ultimately it was better than some regency historicals that I've read just b/c it was a Julia Quinn novel, but I felt like I basically read the same novel twice with a bit of a different ending, and it made the ending feel very rushed also. I hate to be disappointed in a favorite author, but I definitely was this time. I have higher hopes for What Happens in London and hope that this was just an whim on the authors part and won't be repeated in future novels. The only Julia Quinn novel to ever disappoint me! 0 List(won, go, much, dislik, format, stori, took, place, simultani, lost, duke, wyndham, suffic, say, make,

## Exploratory Analysis

In [0]:
# Let's use Spark SQL for some simple exploratory analysis. Firstly, we need to create a temporary view based on the dataframe.

amazon_review_cleaned.createOrReplaceTempView("amazon_book_reviews")

In [0]:
# Distribution of the star ratings of book reviews

star_rating = spark.sql('''
  SELECT 
    overall AS star_rating, 
    COUNT(*) AS count 
  FROM
    amazon_book_reviews
  GROUP BY
    overall
  ORDER BY
    overall
''')

display(star_rating)

star_rating count 1.0 39263 2.0 34276 3.0 64606 4.0 135849 5.0 496584

In [0]:
# Number of reviews over time

review_over_time = spark.sql('''
  SELECT 
    reviewTime AS date, 
    COUNT(*) AS count 
  FROM
    amazon_book_reviews
  WHERE
    reviewTime >= '2015-01-01'
  GROUP BY
    reviewTime
  ORDER BY
    reviewTime
''')

display(review_over_time)

date count 2015-01-01 748 2015-01-02 578 2015-01-03 828 2015-01-04 708 2015-01-05 725 2015-01-06 514 2015-01-07 727 2015-01-08 501 2015-01-09 580 2015-01-10 568 2015-01-11 572 2015-01-12 640 2015-01-13 547 2015-01-14 580 2015-01-15 512 2015-01-16 484 2015-01-17 363 2015-01-18 490 2015-01-19 459 2015-01-20 549 2015-01-21 445 2015-01-22 539 2015-01-23 379 2015-01-24 363 2015-01-25 393 2015-01-26 421 2015-01-27 369 2015-01-28 515 2015-01-29 444 2015-01-30 348 2015-01-31 403 2015-02-01 376 2015-02-02 526 2015-02-03 371 2015-02-04 569 2015-02-05 451 2015-02-06 420 2015-02-07 340 2015-02-08 441 2015-02-09 509 2015-02-10 413 2015-02-11 543 2015-02-12 418 2015-02-13 437 2015-02-14 455 2015-02-15 464 2015-02-16 539 2015-02-17 613 2015-02-18 621 2015-02-19 581 2015-02-20 941 2015-02-21 635 2015-02-22 615 2015-02-23 638 2015-02-24 586 2015-02-25 584 2015-02-26 579 2015-02-27 516 2015-02-28 662 2015-03-01 534 2015-03-02 623 2015-03-03 605 2015-03-04 546 2015-03-05 498 2015-03-06 464 2015-03-07 479 2015-03-08 396 2015-03-09 539 2015-03-10 655 2015-03-11 523 2015-03-12 443 2015-03-13 428 2015-03-14 428 2015-03-15 446 2015-03-16 475 2015-03-17 457 2015-03-18 528 2015-03-19 518 2015-03-20 457 2015-03-21 423 2015-03-22 394 2015-03-23 465 2015-03-24 437 2015-03-25 423 2015-03-26 531 2015-03-27 442 2015-03-28 313 2015-03-29 466 2015-03-30 506 2015-03-31 440 2015-04-01 355 2015-04-02 444 2015-04-03 418 2015-04-04 371 2015-04-05 330 2015-04-06 453 2015-04-07 429 2015-04-08 384 2015-04-09 422 2015-04-10 434 2015-04-11 438 2015-04-12 344 2015-04-13 446 2015-04-14 415 2015-04-15 424 2015-04-16 416 2015-04-17 376 2015-04-18 297 2015-04-19 470 2015-04-20 435 2015-04-21 437 2015-04-22 381 2015-04-23 448 2015-04-24 395 2015-04-25 364 2015-04-26 372 2015-04-27 321 2015-04-28 303 2015-04-29 555 2015-04-30 462 2015-05-01 307 2015-05-02 308 2015-05-03 370 2015-05-04 466 2015-05-05 322 2015-05-06 409 2015-05-07 445 2015-05-08 417 2015-05-09 338 2015-05-10 316 2015-05-11 449 2015-05-12 440 2015-05-13 304 2015-05-14 362 2015-05-15 439 2015-05-16 320 2015-05-17 400 2015-05-18 512 2015-05-19 429 2015-05-20 321 2015-05-21 374 2015-05-22 252 2015-05-23 321 2015-05-24 324 2015-05-25 340 2015-05-26 428 2015-05-27 397 2015-05-28 295 2015-05-29 446 2015-05-30 572 2015-05-31 347 2015-06-01 365 2015-06-02 301 2015-06-03 556 2015-06-04 406 2015-06-05 350 2015-06-06 331 2015-06-07 264 2015-06-08 542 2015-06-09 447 2015-06-10 404 2015-06-11 485 2015-06-12 327 2015-06-13 257 2015-06-14 349 2015-06-15 396 2015-06-16 466 2015-06-17 354 2015-06-18 381 2015-06-19 347 2015-06-20 324 2015-06-21 335 2015-06-22 389 2015-06-23 449 2015-06-24 321 2015-06-25 347 2015-06-26 457 2015-06-27 360 2015-06-28 403 2015-06-29 357 2015-06-30 330 2015-07-01 316 2015-07-02 270 2015-07-03 326 2015-07-04 401 2015-07-05 327 2015-07-06 415 2015-07-07 312 2015-07-08 428 2015-07-09 545 2015-07-10 426 2015-07-11 342 2015-07-12 313 2015-07-13 479 2015-07-14 428 2015-07-15 377 2015-07-16 422 2015-07-17 345 2015-07-18 419 2015-07-19 385 2015-07-20 449 2015-07-21 471 2015-07-22 503 2015-07-23 405 2015-07-24 349 2015-07-25 342 2015-07-26 303 2015-07-27 425 2015-07-28 376 2015-07-29 376 2015-07-30 448 2015-07-31 411 2015-08-01 346 2015-08-02 320 2015-08-03 340 2015-08-04 470 2015-08-05 415 2015-08-06 444 2015-08-07 371 2015-08-08 329 2015-08-09 388 2015-08-10 475 2015-08-11 370 2015-08-12 416 2015-08-13 353 2015-08-14 384 2015-08-15 403 2015-08-16 338 2015-08-17 454 2015-08-18 450 2015-08-19 311 2015-08-20 396 2015-08-21 362 2015-08-22 394 2015-08-23 314 2015-08-24 442 2015-08-25 394 2015-08-26 354 2015-08-27 459 2015-08-28 326 2015-08-29 316 2015-08-30 377 2015-08-31 444 2015-09-01 397 2015-09-02 422 2015-09-03 340 2015-09-04 361 2015-09-05 364 2015-09-06 280 2015-09-07 399 2015-09-08 402 2015-09-09 414 2015-09-10 419 2015-09-11 374 2015-09-12 359 2015-09-13 326 2015-09-14 411 2015-09-15 357 2015-09-16 370 2015-09-17 329 2015-09-18 320 2015-09-19 295 2015-09-20 254 2015-09-21 337 2015-09-22 359 2015-09-23 337

## Review Score Prediction

As comparison, without Spark we commonly use sklearn in Python for machine learning (read more: https://scikit-learn.org/stable/user_guide.html); or NLTK for natural language processing (read more: https://www.nltk.org/)

In [0]:
# Extract verified 5-star and 1-star reviews for prediction

prediction_df = amazon_review_cleaned.where( ((amazon_review_cleaned.overall == 1) | (amazon_review_cleaned.overall == 5)) \
                                             & amazon_review_cleaned.verified == True )

# This is equivalent to the following Spark SQL command:

prediction_df = spark.sql("SELECT * FROM amazon_book_reviews WHERE (overall = 1 OR overall = 5) AND verified = TRUE")

display(prediction_df)

reviewID overall verified reviewTime reviewerID asin reviewerName reviewText summary label reviewWordCleaned 984583 5.0 true 2018-05-07 A101RVZV3RBT8O B000BRU78C James Rizer heavy duty, great thermos. great thermos. 0 List(heavi, duti, great, thermo) 1726599 5.0 true 2016-01-06 A103CUDJVYLAHR B000UBO0IW Amazon Customer These were perfect. I have 4 grandchildren and I give each one an ornament each year. These just fit the bill. These were perfect. I have 4 grandchildren and I give each ... 0 List(perfect, 4, grandchildren, give, one, ornament, year, fit, bill) 2084214 5.0 true 2017-12-29 A104L4I6JM259S B0017XHSC2 Cory Stamm Works great Five Stars 0 List(work, great) 68080 5.0 true 2017-02-06 A1095ORFAE5XEA B00004RFM0 Cyrus Douglas The j. A. Henckels knives are very sharp. Just what I wanted The j. A. Henckels knives are very sharp ... 0 List(j, henckel, knive, sharp, want) 2330799 5.0 true 2014-12-28 A10AGLJYHNUKZA B001A60SXW Miss G Somehow there is a draft that is coming through my walls. How does that happen? I purchased these curtains for the insulation. They are a very close match to the color of my walls. Imagine a wall with 2 standard windows with the normal space between them. I hung the curtains on a rod stretched between the 2 windows. It actually looks nice (Not tacky like my daughter said it would.) More important, it cut the draft. No More Wall Draft 0 List(somehow, draft, come, wall, happen, purchas, curtain, insul, close, match, color, wall, imagin, wall, 2, standard, window, normal, space, hung, curtain, rod, stretch, 2, window, actual, look, nice, tacki, like, daughter, said, import, cut, draft) 1022610 5.0 true 2016-11-30 A10I77K5M5ZO4H 0025853503 Kelsy Bellah Pat Conroy's Preface to this novel is just precious and inspiring. A note every mother should be proud to read. Classic 0 List(pat, conroy, prefac, novel, preciou, inspir, note, everi, mother, proud, read) 227649 5.0 true 2010-12-27 A10K4042PZXP0X B000FQBF1M Kenny Parker Similar in scope to Call of Duty. Some of the scenarios require problem solving skills to defeat the foes. For the most part, this is a rock em sock em kick ass game that will get your heart beat up and challenge your trigger finger. I like it enough to pre-order KILLZONE 3. Killzone GREAT 0 List(similar, scope, call, duti, scenario, requir, problem, solv, skill, defeat, foe, part, rock, em, sock, em, kick, ass, game, get, heart, beat, challeng, trigger, finger, like, enough, pre, order, killzon, 3) 2849493 5.0 true 2015-04-13 A10KA8JQ0MK4IN B003AM896W Gisela Spencer This is a good quality container. I haven't teted the bean freshness as I just got it but looks easy to use. Looking forward to fresh beans 0 List(good, qualiti, contain, haven, tete, bean, fresh, got, look, easi, use) 540581 5.0 true 2017-06-21 A10KZZ7BQ80UW8 B0000CFTPI rl plastic is cheaper if you are on a tight budget, but even though it can chip or break, the pyrex is so much more sanitary and functional (freezer, microwave, etc.), it is my preferred method for temporary storage of food items, by far. this size is good for a hefty meal, and the lid is airtight, although it (the lid) cannot withstand extreme heat. this size is good for a hefty meal 0 List(plastic, cheaper, tight, budget, even, though, chip, break, pyrex, much, sanitari, function, freezer, microwav, etc, prefer, method, temporari, storag, food, item, far, size, good, hefti, meal, lid, airtight, although, lid, withstand, extrem, heat) 1306268 1.0 true 2014-12-04 A10MTJCHE99UBA B000IMYID0 Indiana Cheryl Handle broke off the first time I washed it in my sink. I was issued a refund. Microwave Corn Popper 0 List(handl, broke, first, time, wash, sink, issu, refund) 1801357 5.0 true 2014-04-08 A10QTFGDSIRV5W 006113399X K. Adele One of Nesbo's solid skills is to employ a non-linear approach to time. In The Redbreast, an obvious use of this skill is to interlace events at the front during World War II with current events. There is nothing unique a about alternating

In [0]:
# Take a stratified sample

print("Number of rows before sampling: ", prediction_df.count())
prediction_df_sampled = prediction_df.sampleBy("overall", fractions = {1:0.001, 5:0.001}, seed = 16).cache()
print("Number of rows after sampling: ", prediction_df_sampled.count())

Number of rows before sampling:  449388
Number of rows after sampling:  478


### TF-IDF with Hashing Trick + Random Forest

In [0]:
# Copy prediction data

prediction_tfidf_hash = prediction_df_sampled.select('*')

In [0]:
# Extract bigram

from pyspark.ml.feature import NGram
from pyspark.sql.functions import array_union

ngram = NGram(n = 2, inputCol="reviewWordCleaned", outputCol="reviewBigrams")
prediction_tfidf_hash = ngram.transform(prediction_tfidf_hash)

prediction_tfidf_hash = prediction_tfidf_hash.withColumn("reviewNgrams", \
                                                         array_union(prediction_tfidf_hash.reviewWordCleaned, \
                                                                     prediction_tfidf_hash.reviewBigrams))

In [0]:
# Getting tf-idf values for 1-2grams

from pyspark.ml.feature import HashingTF, IDF

hashtf = HashingTF(numFeatures=2**12, inputCol="reviewNgrams", outputCol='TF')
tf = hashtf.transform(prediction_tfidf_hash)
idf = IDF(minDocFreq=3, inputCol="TF", outputCol="TF-IDF")
idfModel = idf.fit(tf)
prediction_tfidf_hash = idfModel.transform(tf)

In [0]:
display(prediction_tfidf_hash)

reviewID overall verified reviewTime reviewerID asin reviewerName reviewText summary label reviewWordCleaned reviewBigrams reviewNgrams TF TF-IDF 1981107 1.0 true 2010-05-10 A2TMEJ22IET200 0061656100 truth is logical Wow, after reading all the raving reviews on this one, I figured I couldn't possibly go wrong. Was I ever sorely mistaken. This was the first book by Elizabeth Peters I've read. The main character wasn't even slightly likable. She was a loose, sarcastic and mean person. The only reason the reader might root for her would be just to get the mystery solved. The other characters were shallow and insincere. There were so many loose ends that the whole story was unsatisfying. The concluding paragraphs even admit that there are many loose ends "that we will never know." How lame is that? If you enjoy a mystery that actually gives you clues so that you can at least begin to piece the mystery together, then this book is not for you. Nothing in the book allows the reader to piece it together (the author doesn't even piece it together). On the other hand, if you enjoy just following the arbitrary actions of a shallow woman who toys with her affections, then knock yourself out. The greatest mystery is why I bothered to finish the book. (Guess I kept hoping there'd be some great finale.) Not even enjoyable. 1 List(wow, read, rave, review, one, figur, couldn, possibl, go, wrong, ever, sore, mistaken, first, book, elizabeth, peter, ve, read, main, charact, wasn, even, slightli, likabl, loos, sarcast, mean, person, reason, reader, might, root, get, mysteri, solv, charact, shallow, insincer, mani, loos, end, whole, stori, unsatisfi, conclud, paragraph, even, admit, mani, loos, end, never, know, lame, enjoy, mysteri, actual, give, clue, least, begin, piec, mysteri, togeth, book, noth, book, allow, reader, piec, togeth, author, doesn, even, piec, togeth, hand, enjoy, follow, arbitrari, action, shallow, woman, toy, affect, knock, greatest, mysteri, bother, finish, book, guess, kept, hope, d, great, final) List(wow read, read rave, rave review, review one, one figur, figur couldn, couldn possibl, possibl go, go wrong, wrong ever, ever sore, sore mistaken, mistaken first, first book, book elizabeth, elizabeth peter, peter ve, ve read, read main, main charact, charact wasn, wasn even, even slightli, slightli likabl, likabl loos, loos sarcast, sarcast mean, mean person, person reason, reason reader, reader might, might root, root get, get mysteri, mysteri solv, solv charact, charact shallow, shallow insincer, insincer mani, mani loos, loos end, end whole, whole stori, stori unsatisfi, unsatisfi conclud, conclud paragraph, paragraph even, even admit, admit mani, mani loos, loos end, end never, never know, know lame, lame enjoy, enjoy mysteri, mysteri actual, actual give, give clue, clue least, least begin, begin piec, piec mysteri, mysteri togeth, togeth book, book noth, noth book, book allow, allow reader, reader piec, piec togeth, togeth author, author doesn, doesn even, even piec, piec togeth, togeth hand, hand enjoy, enjoy follow, follow arbitrari, arbitrari action, action shallow, shallow woman, woman toy, toy affect, affect knock, knock greatest, greatest mysteri, mysteri bother, bother finish, finish book, book guess, guess kept, kept hope, hope d, d great, great final) List(wow, read, rave, review, one, figur, couldn, possibl, go, wrong, ever, sore, mistaken, first, book, elizabeth, peter, ve, main, charact, wasn, even, slightli, likabl, loos, sarcast, mean, person, reason, reader, might, root, get, mysteri, solv, shallow, insincer, mani, end, whole, stori, unsatisfi, conclud, paragraph, admit, never, know, lame, enjoy, actual, give, clue, least, begin, piec, togeth, noth, allow, author, doesn, hand, follow, arbitrari, action, woman, toy, affect, knock, greatest, bother, finish, guess, kept, hope, d, great, final, wow read, read rave, rave review, review one, one figur, figur couldn, couldn possibl, possibl go, go wrong, wrong ev

In [0]:
# Random Forest

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="overall", outputCol="indexedScore").fit(prediction_tfidf_hash)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="TF-IDF", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

(trainingData, testData) = prediction_tfidf_hash.randomSplit([0.7, 0.3])

rf_model = pipeline.fit(trainingData)
predictions = rf_model.transform(testData)


In [0]:
display(predictions.select("overall", "indexedScore", "rawPrediction", "probability", "prediction", "predictedLabel"))

overall indexedScore rawPrediction probability prediction predictedLabel 1.0 1.0 Map(vectorType -> dense, length -> 2, values -> List(33.56263223286718, 6.437367767132829)) Map(vectorType -> dense, length -> 2, values -> List(0.8390658058216793, 0.1609341941783207)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(36.61545191490311, 3.3845480850968883)) Map(vectorType -> dense, length -> 2, values -> List(0.9153862978725777, 0.08461370212742221)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(36.944508319845646, 3.055491680154349)) Map(vectorType -> dense, length -> 2, values -> List(0.9236127079961413, 0.07638729200385873)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.25225946542667, 1.7477405345733374)) Map(vectorType -> dense, length -> 2, values -> List(0.9563064866356665, 0.04369351336433343)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(37.26652810078599, 2.733471899214008)) Map(vectorType -> dense, length -> 2, values -> List(0.9316632025196497, 0.0683367974803502)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(37.570133711008864, 2.429866288991137)) Map(vectorType -> dense, length -> 2, values -> List(0.9392533427752217, 0.06074665722477842)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.24315754260874, 1.7568424573912607)) Map(vectorType -> dense, length -> 2, values -> List(0.9560789385652185, 0.043921061434781514)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.21759843717743, 1.7824015628225707)) Map(vectorType -> dense, length -> 2, values -> List(0.9554399609294357, 0.044560039070564265)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(37.25305943008523, 2.746940569914769)) Map(vectorType -> dense, length -> 2, values -> List(0.9313264857521307, 0.06867351424786923)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(38.25342905606994, 1.7465709439300625)) Map(vectorType -> dense, length -> 2, values -> List(0.9563357264017485, 0.04366427359825156)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, values -> List(28.820716254219548, 11.179283745780456)) Map(vectorType -> dense, length -> 2, values -> List(0.7205179063554887, 0.2794820936445114)) 0.0 5.0 5.0 0.0 Map(vectorType -> dense, length -> 2, 

In [0]:
# Calculate AUC for train/test split

from pyspark.ml.evaluation import BinaryClassificationEvaluator

evaluator = BinaryClassificationEvaluator(labelCol="indexedScore", metricName="areaUnderROC")
auc = evaluator.evaluate(predictions)
print("AUC = %g" % auc)

AUC = 0.783126


In [0]:
# Performance evaluation with 5-fold cross validation

from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

evaluator = BinaryClassificationEvaluator(labelCol="indexedScore", metricName="areaUnderROC")
auc = evaluator.evaluate(predictions)
paramGrid = ParamGridBuilder().build()
cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, numFolds=5)
cvModel = cv.fit(prediction_tfidf_hash)

print("Average AUC = %g" % cvModel.avgMetrics[0])

Average AUC = 0.491531


### Doc2Vec + Random Forest

In [0]:
# Copy prediction data

prediction_doc2vec = prediction_df_sampled.select('*')

In [0]:
# Calculate Doc2Vec

from pyspark.ml.feature import Word2Vec

word2Vec = Word2Vec(inputCol="reviewWordCleaned", outputCol="doc2vec")
w2v_model = word2Vec.fit(prediction_doc2vec)

prediction_doc2vec = w2v_model.transform(prediction_doc2vec)

In [0]:
display(prediction_doc2vec)

reviewID overall verified reviewTime reviewerID asin reviewerName reviewText summary label reviewWordCleaned doc2vec 1981107 1.0 true 2010-05-10 A2TMEJ22IET200 0061656100 truth is logical Wow, after reading all the raving reviews on this one, I figured I couldn't possibly go wrong. Was I ever sorely mistaken. This was the first book by Elizabeth Peters I've read. The main character wasn't even slightly likable. She was a loose, sarcastic and mean person. The only reason the reader might root for her would be just to get the mystery solved. The other characters were shallow and insincere. There were so many loose ends that the whole story was unsatisfying. The concluding paragraphs even admit that there are many loose ends "that we will never know." How lame is that? If you enjoy a mystery that actually gives you clues so that you can at least begin to piece the mystery together, then this book is not for you. Nothing in the book allows the reader to piece it together (the author doesn't even piece it together). On the other hand, if you enjoy just following the arbitrary actions of a shallow woman who toys with her affections, then knock yourself out. The greatest mystery is why I bothered to finish the book. (Guess I kept hoping there'd be some great finale.) Not even enjoyable. 1 List(wow, read, rave, review, one, figur, couldn, possibl, go, wrong, ever, sore, mistaken, first, book, elizabeth, peter, ve, read, main, charact, wasn, even, slightli, likabl, loos, sarcast, mean, person, reason, reader, might, root, get, mysteri, solv, charact, shallow, insincer, mani, loos, end, whole, stori, unsatisfi, conclud, paragraph, even, admit, mani, loos, end, never, know, lame, enjoy, mysteri, actual, give, clue, least, begin, piec, mysteri, togeth, book, noth, book, allow, reader, piec, togeth, author, doesn, even, piec, togeth, hand, enjoy, follow, arbitrari, action, shallow, woman, toy, affect, knock, greatest, mysteri, bother, finish, book, guess, kept, hope, d, great, final) Map(vectorType -> dense, length -> 100, values -> List(-0.004688795161200687, 0.01183068166886057, 0.011641626414362987, -0.014178378124987439, 3.651971667434792E-4, 0.01043624402919537, -0.002648466687212337, 0.011437084357140167, -0.010252108643002503, -0.010576695449678796, 0.006783989714862474, -0.007940840777912538, 0.002149063861591513, -0.0067340118961399225, 0.002376375209102977, -0.008385658365132628, -0.015239988056923812, -0.016427046994735694, 0.002377903965011961, -1.9210219345820533E-4, 0.0036844007281244405, -0.010543926984870007, -6.770662475158745E-4, -0.005163045463446831, 0.005306382121860373, 0.0017524700058263022, -0.007154896554218757, -0.0011933446598681144, -0.009554780506509906, 2.8877555198459026E-4, -0.01176074346140198, 0.004740216064252605, -0.0055250332326086575, 0.002053321352257032, -0.003579194172242732, 0.013346121152886664, -0.004576148375885427, 0.008773214705240893, 0.01004636330572812, -0.011910343606842263, 3.2143836996306627E-4, -0.011566822647535223, 1.3272936900778274E-4, -0.01584239531075582, 0.011358153244851118, 0.0014308289380040855, -0.007238188117020288, 4.343941854669389E-5, -0.004376419250287913, -0.004352399013515999, 0.00869433792802144, 0.007960275047202118, 0.004645183833009487, -2.919943881908916E-4, -7.030844459148618E-4, -0.0020629570092435697, -0.010789652366894392, -0.006105925894950573, 0.0018293077431438603, -0.0022900022595422342, 0.006853842954282002, -0.0022683619240617225, 0.010058533218546713, 8.969037107260878E-4, -0.009030778609615351, 0.012207700535940119, 0.006980669177172952, -0.003988481610799588, -0.001323521018446404, -0.0040401957224702875, 0.001380632760591819, 0.01230161621446759, -0.0013651180746893834, 0.0011547191906898587, -0.0033304156629815314, 0.0011624071618770153, 0.002211298000029459, -0.0052688421039457185, -0.0015124635469781385, 0.004961100196684425, 0.0013774160301070469, 0.0015924506486935197, -0.002475647247462932, -0.005584518165013999, -0.018404739894619097, 0.024563

In [0]:
# Random Forest

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="overall", outputCol="indexedScore").fit(prediction_doc2vec)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="doc2vec", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

(trainingData, testData) = prediction_doc2vec.randomSplit([0.7, 0.3])

rf_model = pipeline.fit(trainingData)
predictions = rf_model.transform(testData)

from pyspark.ml.evaluation import BinaryClassificationEvaluator

evaluator = BinaryClassificationEvaluator(labelCol="indexedScore", metricName="areaUnderROC")
auc = evaluator.evaluate(predictions)
print("AUC = %g" % auc)

AUC = 0.663221


In [0]:
# Performance evaluation with 10-fold cross validation

from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

paramGrid = ParamGridBuilder().build()
cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, numFolds=5)
cvModel = cv.fit(prediction_doc2vec)

print("Average AUC = %g" % cvModel.avgMetrics[0])

Average AUC = 0.740104


## Model Interpretation

In [0]:
# Extract bigram

interpret_tfidf = prediction_df_sampled.select('*')

from pyspark.ml.feature import NGram
from pyspark.sql.functions import array_union

ngram = NGram(n = 2, inputCol="reviewWordCleaned", outputCol="reviewBigrams")
interpret_tfidf = ngram.transform(interpret_tfidf)

interpret_tfidf = interpret_tfidf.withColumn("reviewNgrams", \
                                             array_union(interpret_tfidf.reviewWordCleaned, \
                                                         interpret_tfidf.reviewBigrams))

In [0]:
# Calculating TF-IDF without hashing; limit vocabulary to top 2^12 (4096) ngrams

from pyspark.ml.feature import CountVectorizer, IDF

tf = CountVectorizer(inputCol="reviewNgrams", outputCol='TF', minDF=2.0, vocabSize=2**12)
tf_model = tf.fit(interpret_tfidf)
tf_transformed = tf_model.transform(interpret_tfidf)
idf = IDF(minDocFreq=3, inputCol="TF", outputCol="TF-IDF")
idfModel = idf.fit(tf_transformed)
interpret_tfidf = idfModel.transform(tf_transformed)

In [0]:
# Building a full Random Forest model with all the data, using TF-IDF embedding without hashing

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="overall", outputCol="indexedScore").fit(interpret_tfidf)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="TF-IDF", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

rf_model = pipeline.fit(interpret_tfidf)

In [0]:
# Getting feature importance from the Random Forest model

feature_importance = rf_model.stages[-2].featureImportances
print(feature_importance)

(1561,[0,1,3,4,6,7,8,10,11,12,15,19,22,26,28,30,32,33,34,35,36,39,47,48,50,58,59,61,62,63,67,72,74,76,77,78,80,81,83,85,93,98,99,101,104,105,106,107,121,132,136,139,141,143,145,152,156,160,162,171,174,177,183,189,193,195,198,199,203,212,218,219,222,230,232,235,243,245,249,250,258,270,276,281,282,283,300,301,306,312,318,325,327,331,341,343,345,348,352,357,363,365,371,376,378,379,393,394,402,404,406,410,413,416,418,419,420,426,442,444,447,458,463,464,468,471,476,477,478,479,480,486,499,504,507,510,513,518,523,547,554,556,560,562,576,578,586,591,598,604,606,609,623,625,627,630,631,635,637,640,643,646,651,657,661,670,679,686,689,690,691,696,699,707,713,720,727,729,730,738,741,746,766,798,799,803,805,824,835,837,838,840,847],[0.0054539613749843945,0.005181292143884781,0.0012461925025749633,0.0023203791406947575,0.0153756697928116,0.0020945244436419456,0.004705249313787477,0.006030517379756843,0.0037701439985555014,0.0030304903405075387,0.003072861203386884,0.0037265903867781495,0.0066125844

In [0]:
# Get the top 20 most important feature's indices, and its importance metric

import numpy as np
import pandas as pd

top20_indice = np.flip(np.argsort(feature_importance.toArray()))[:20].tolist()
top20_importance = []
for index in top20_indice:
    top20_importance.append(feature_importance[index])

top20_df = spark.createDataFrame(pd.DataFrame(list(zip(top20_indice, top20_importance)), columns =['index', 'importance']))

display(top20_df)

index importance 331 0.030833967044159298 670 0.028372773440812078 803 0.024458734193047334 606 0.02445437188866429 847 0.023200308051610805 152 0.021003902238539842 345 0.020791139167101787 643 0.017706677021853485 199 0.01700319063633082 738 0.015473498626258363 6 0.0153756697928116 402 0.015017092855770473 696 0.014618329124846391 98 0.014242981563094989 85 0.014025678966185617 219 0.013952093003165892 690 0.013763368628069548 77 0.013223824773063173 637 0.013000072248036319 640 0.012817783592927068

In [0]:
# Create a map between each ngram and its index

from pyspark.sql.functions import explode, udf, col
from pyspark.sql.types import *

make_list_udf = udf(lambda col: [col], ArrayType(StringType()))
remove_list_udf = udf(lambda col: col[0], StringType())

def get_index(col):
    if len(col.indices) == 0:
        return -1   # Mark the ngram's index as -1 if it is not the top 2^12 ngrams
    else:
        return int(col.indices[0])
get_index_udf = udf(get_index, IntegerType())

ngram_index = interpret_tfidf.select(explode(interpret_tfidf.reviewNgrams).alias("reviewNgrams")).distinct() \
                             .withColumn("reviewNgrams", make_list_udf("reviewNgrams"))
ngram_index = tf_model.transform(ngram_index)
ngram_index = ngram_index.withColumn("reviewNgrams", remove_list_udf("reviewNgrams")) \
                         .withColumn("index", get_index_udf("TF")) \
                         .select("reviewNgrams", "index")

In [0]:
display(ngram_index.where(ngram_index.index > -1))

reviewNgrams index hope 152 stori 19 even 48 first book 1124 piec 98 hand 72 noth 499 wasn 450 allow 568 togeth 252 rave review 1419 main 1535 wow 1283 action 1303 reader 315 one 1 person 230 read 9 author 274 woman 664 great 0 kept 670 reason 150 go 25 wrong 402 admit 741 shallow 949 end 107 enjoy 56 loos 1560 d 288 doesn 189 whole 239 never know 1465 mean 233 actual 143 ve 30 never 40 main charact 1360 follow 250 clue 1479 couldn 314 sore 625 go wrong 840 knock 940 figur 419 slightli 459 final 164 finish 327 review 85 mysteri 442 least 445 mani 36 get 14 possibl 1011 begin 575 review one 1050 charact 102 know 77 first 41 give 211 might 518 book 4 ever 55 rave 1247 guess 415 stove 821 got 88 two 81 burn 1080 sturdi 83 put 106 non 361 perfectli 87 amazon 62 vacuum 342 fine 289 pleas 180 nice big 1254 good product 496 pleas purchas 1557 packag 269 cover 197 first one 396 match 272 work perfectli 425 bought 17 rack 1204 cleaner 658 find 89 work 8 price 32 find size 1189 call 275 vacuum cleaner 980 great price 599 cover work 1390 bag 162 spare 1238 good 5 nice 21 sear 752 purchas 26 wood 411 work fine 581 product 20 nice sturdi 602 size 42 keep 31 less 205 big 110 gave 590 travel 394 histor 810 fact 139 captiv 1495 well written 474 research 476 grade 851 love 2 great qualiti 747 dish 490 take 45 excel 75 blow 1017 stainless 148 steel 179 stainless steel 220 book stori 863 color 185 like 7 look 16 complaint 559 small 59 satisfi 427 husband 182 well 6 sleep 373 fan 280 base 449 written 218 recommend 13 true 678 qualiti 34 gameplay 574 read children 1115 left 332 fun 64 classic 194 control 120 love book 324 smooth 225 mission 860 child 700 divers 1207 children 594 beat 818 pick 577 classic love 1156 graphic 170 space 138 new 46 solid 261 kitchen 117 favorit 135 amaz 94 thing 43 highli recommend 91 highli 73 get one 598 cut 166 huge 325 never read 778 heard book 1492 realli 11 year old 400 one bought 640 expect first 1333 superb 809 difficult 417 languag 771 writer 850 told 356 bought niec 921 centuri 1094 larg 192 eye 806 glad 240 french 1048 famili 116 old 66 life 86 niec 757 use 3 expect 69 year 28 comfort 406 colleg 1336 much 18 wee 1113 babi 262 edg 296 wee one 981 heard 548 english 1284 understand 258 unusu 1044 modern 1089 though 210 excess 1379 even though 808 ador 1198 awhil 732 purchas onlin 993 go bed 1517 book make 1402 consid 524 reason price 1417 bean 1405 ceram 1313 back 58 wide 471 saw 632 hear 856 recent 623 recommend product 645 differ 80 great read 339 tell 579 peopl 165 avail 363 onlin 714 decid purchas 1253 look forward 1023 book ve 1025 easier 255 night 300 e 1450 love love 783 also good 662 slim 550 con 462 camp 855 pro 473 cup 308 support 943 soft 421 frequent 1309 break 452 took 237 forward 1464 brought back 1425 due 472 alreadi 267 want 33 ve actual 963 decid 217 correct 726 everi 61 make 15 hard 188 broke 345 fill 593 lot 65 part 126 storag 399 small size 1155 store 178 help 176 mini 838 bed 293 time 10 replac part 882 attach 424 sometim 1097 copi 1203 replac 100 year back 858 drop 364 diamet 684 handl 114 read year 1493 brought 1540 also 38 plastic 174 collect 572 conveni 711 scale 601 perfect 23 buy 22 sure 136 america 736 hanger 1163 job 169 work great 127 test kitchen 872 better 39 best book 1092 one best 337 best 37 perfect job 862 right 63 cloth 1158 test 805 ever written 972 america test 1397 thank 196 psp 1422 work like 612 aliv 892 brand 149 brand new 338 often 305 avid 1038 teacher 913 valuabl 1169 check 669 book read 386 receiv 306 age 570 item 74 order 47 talk 228 hannah 1193 retir 1369 10 204 gift 95 day 82 stuff 398 none 507 great day 1537 friend 151 filter 404 5 93 read love 1099 frame 1532 super 284 peel 665 sharp 319 friend famili 919 quickli 222 anoth 53 anyth 540 metal 622 satir 1414 day one 1013 ve bought 721 hero 1183 doesnt 520 advertis 693 potato 1307 compani 639 bought gift 1265 disappoint 410 get pay 1127 pay 335 start 119 bedroom 317 construct 1475 theme 958 simpl 216 thought 124 g

In [0]:
# Find the ngrams that map to the top 20 most important features

# Note that if you used hashingTF for word embedding, there would be multiple ngrams under the same index, because of the collision introduced by hashing, all of which would share and contribute to one importance score, and we don't have a way to separate their contribution to the importance score.
# Here in order to avoid such collision (so just one index per ngram), I used CountVectorizer instead of HashingTF during encoding.

import pyspark.sql.functions as f

top20_ngram = top20_df.join(ngram_index, on="index", how="left_outer")
display(top20_ngram.groupby("importance").agg(f.collect_list(top20_ngram.reviewNgrams).alias("reviewNgrams")).orderBy("importance", ascending=False))

importance reviewNgrams 0.030833967044159298 List(return) 0.028372773440812078 List(kept) 0.024458734193047334 List(front) 0.02445437188866429 List(junk) 0.023200308051610805 List(slide) 0.021003902238539842 List(hope) 0.020791139167101787 List(broke) 0.017706677021853485 List(com) 0.01700319063633082 List(cheap) 0.015473498626258363 List(crap) 0.0153756697928116 List(well) 0.015017092855770473 List(wrong) 0.014618329124846391 List(apart) 0.014242981563094989 List(piec) 0.014025678966185617 List(review) 0.013952093003165892 List(bad) 0.013763368628069548 List(fell) 0.013223824773063173 List(know) 0.013000072248036319 List(xbox) 0.012817783592927068 List(one bought)